In [21]:
import pandas as pd
from kmodes.kprototypes import KPrototypes
from sklearn.preprocessing import StandardScaler
import folium
from folium.plugins import MarkerCluster

In [5]:
df = pd.read_csv("enviroTab_pa_train.csv", sep=';')
df_sans_na = df.dropna()
df_sans_na.reset_index(inplace=True, drop=True)

In [6]:
quanti = df_sans_na.iloc[:,9:37]
variables_quantitatives = quanti.apply(lambda col: col.fillna(col.mean()), axis=0)

In [8]:
quanti.head()

bio1  bio2  bio3  bio4  bio5  bio6  bio7  bio8  bio9  bio10  ...  bio19  \
0  2878    95  3.33  6635  3032  2747   285  2880  2967   2967  ...   1559   
1  2878    95  3.33  6635  3032  2747   285  2880  2967   2967  ...   1559   
2  2878    95  3.33  6635  3032  2747   285  2880  2967   2967  ...   1559   
3  2876    95  3.33  6614  3031  2746   285  2879  2965   2965  ...   1603   
4  2877    95  3.33  6635  3031  2746   285  2879  2966   2966  ...   1586   

         bdod         cec        cfvo        clay    nitrogen      phh2o  \
0  142.439041  192.611618  173.934845  244.970306  184.283295  75.167183   
1  142.439041  192.611618  173.934845  244.970306  184.283295  75.167183   
2  142.439041  192.611618  173.934845  244.970306  184.283295  75.167183   
3  139.343964  201.281235  184.239105  223.070511  221.730957  73.108734   
4  145.295364  195.884705  171.115875  234.305283  195.522888  74.028191   

         sand        silt         soc  
0  379.648071  374.968933  226.862244  
1  379.648071  374.968933  226.862244  
2  379.648071  374.968933  226.862244  
3  378.273560  398.929901  255.015320  
4  382.905090  382.355530  241.613922  

[5 rows x 28 columns]

In [9]:
quali = df_sans_na[['landCov','Popdensity2010', 'Built2009', 'Lights2009', 'Railways', 'Roads']]
variables_qualitatives = quali.apply(lambda col: col.fillna(col.mode()[0]), axis=0)

In [32]:
scaler = StandardScaler()
variables_quantitatives_standardisees = scaler.fit_transform(variables_quantitatives)

# Concaténation des variables quantitatives standardisées et des variables catégorielles
X = pd.concat([pd.DataFrame(variables_quantitatives_standardisees, columns=variables_quantitatives.columns), variables_qualitatives], axis=1)

# Spécification du nombre de clusters (à ajuster)
nombre_clusters = 5

# Application de l'algorithme K-Prototypes
kproto = KPrototypes(n_clusters=nombre_clusters, init='Cao', verbose=2)
clusters = kproto.fit_predict(X, categorical=[X.columns.get_loc(col) for col in variables_qualitatives.columns])

# Ajout des étiquettes de cluster au DataFrame d'origine
df_sans_na['cluster'] = clusters

Initialization method and algorithm are deterministic. Setting n_init to 1.
Init: initializing centroids
Init: initializing clusters
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run: 1, iteration: 1/100, moves: 1842, ncost: 71453.19997299745
Run: 1, iteration: 2/100, moves: 560, ncost: 69519.10574081908
Run: 1, iteration: 3/100, moves: 116, ncost: 69429.21330493859
Run: 1, iteration: 4/100, moves: 21, ncost: 69425.55658912279
Run: 1, iteration: 5/100, moves: 5, ncost: 69425.28146196676
Run: 1, iteration: 6/100, moves: 1, ncost: 69425.24523875833
Run: 1, iteration: 7/100, moves: 0, ncost: 69425.24523875833
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run: 2, iteration: 1/100, moves: 1806, ncost: 71940.82686047992
Run: 2, iteration: 2/100, moves: 645, ncost: 69515.03697793117
Run: 2, iteration: 3/100, moves: 325, ncost: 68203.13092107314
Run: 2, iteration: 4/100, moves: 83, ncost: 68147.71046232489
Run: 2, iteration: 5

C:\Users\Utilisateur\AppData\Local\Temp\ipykernel_12432\312485815.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_sans_na['cluster'] = clusters


In [34]:
import folium

# Supposons que vous avez déjà les résultats et les données de test
# Assurez-vous que les indices correspondent entre result et test_df

# Initialisation des variables pour la carte
m = folium.Map(location=[df_sans_na['lat'].mean(), df_sans_na['lon'].mean()], zoom_start=10)

# Créez une fonction pour attribuer une couleur en fonction du cluster
def assign_color(cluster):
    # Ajoutez autant de couleurs que de clusters possibles
    color_mapping = {
        0: 'lightblue',
        1: 'green',
        2: 'red',
        3: 'purple',
        4: 'darkblue',
        # Ajoutez d'autres couleurs au besoin
    }
    # Utilisez la couleur par défaut si le cluster n'est pas dans la carte
    return color_mapping.get(cluster, 'gray')

# Ajoutez les marqueurs à la carte en utilisant les coordonnées et la couleur du cluster
for index, row in df_sans_na.iterrows():
    cluster_color = assign_color(row['cluster'])
    folium.Marker(
        location=[row['lat'], row['lon']],
        popup=f"Cluster: {row['cluster']}",
        icon=folium.Icon(color=cluster_color)
    ).add_to(m)

# Sauvegardez la carte au format HTML
m.save("carte.html")

# Affichez la carte
m



In [14]:
for val in clusters :
    if val > 0 :
        print(val)

2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
2
2
2
2
2
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
2
1
2
2
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
1
2
2
